# DSS2ETCBC: the lexemes and parts of speech of the biblical scrolls

By Martijn Naaijer and Jarod Jacobs

One of the goals of the CACCHT project is to integrate the scrolls in the ETCBC database by encoding them in the ETCBC format. In a previous blogpost we explained how POS tagging of Hebrew texts can be done using an LSTM network. In this blogpost we show how the lexemes of the words in the biblical scrolls can be converted from the encoding done by Abegg to the ETCBC lexemes.

## General approach

The text-fabric package containing the Dead Sea Scrolls has a variety of word features, such as number, gender, person, and lexeme. Some of these can be converted straightforwardly to ETCBC format. An example is number. We assume that verb forms in the first person in the dss package correspond one to one with the first person in the ETCBC database. 

There are features, for which this correspondence cannot be used straightforwardly. An example is the word feature part of speech. In the dss package there is the value "ptcl" (particle). This value corresponds with "conj" (conjunction), and "prep" (preposition), among other things.

Something similar is going on with the feature lexeme. In the ETCBC database, the lexemes are based on KBL lexicon, but in the course of time a whole range of improvements have been implemented, based on ongoing research. Therefore, it is understandable, that there is not always a one to one correspondence between the lexemes of the dss package and the BHSA.

So, how can we assign the ETCBC values of the feature lexeme to the scrolls? In the case of the biblical scrolls one can simply use lexemes used for the same words in corresponding verses. For instance, the scroll 4Q2 contains the text of Genesis. Its text of verse 1:1 is BR>CJT BR> >LHJM >T HCMJM W>T H>RY, which is identical to the text of Genesis 1:1 in the BHSA. In this case, we can simply give each word the lexeme of the same word in the BHSA. In many cases, however, the text of the scrolls deviates more or less with that of the BHSA.

This problem is solved by using sequence alignment. This means that two strings are arranged in such a way that similar parts are identified. Alignment of sequences is used often in biology, if one wants to identify similarities and differences in DNA strings or proteins. Sequence alignment techniques are often based on dynamic programming, such as the Smith Waterman Algorithm. In the package [biopython](https://towardsdatascience.com/pairwise-sequence-alignment-using-biopython-d1a9d0ba861f) a whole range of algorithms for the study of biological sequences are implemented. We use this package, and the module pairwise2, which is contained in it, to align biblical verses in the DSS and the BHSA.

In practice , this looks as follows. As an example we look at Isaiah 48:2 in the BHSA and 1QIsaa. 

    KJ- M <JR H Q-DC NQR>W W <L >L-HJ JFR>L NSMKW JHWH YB>WT CMW   BHSA
    
    KJ> M <JR H QWDC NQR>W W <L >LWHJ JFR>L NSMKW JHWH YB>WT CMW   1QIsaa


It is clear that the text of the BHSA and 1QIsaa is very similar, but there are also some differences. Similar parts in the verses are put together, resulting in two sequences of equal length. On the place of the extra matres lectiones in 1QIsaa, one finds a gap ("-") in the BHSA.

Now, we look at every character in 1QIsaa, and check the lexeme of the corresponding character in the BHSA. If more than half of the characters in a word in the scroll corresponds with one lexeme in the BHSA, we give the value of this lexeme to the word in the scroll. In the case of the first word in Isaiah 48:2, the K and J correspond to a character in the corresponding word with the lexeme KJ, and the character > does not correspond with a word in the BHSA. The result is that 2 out of 3 characters correspond with the lexeme KJ, which is more than 50%, so the first word KJ> in this verse of the scroll gets the value KJ. This approach works well in practice, but it does not result in a value for each word. 

An example is Isaiah 42:23 in 1QIsaa: 

    MJ- BKM- --J>ZJN Z->T --JQCB W JCM< L >XWR    BHSA

    MJ> BKMH W J>ZJN ZW>T W JQCB W JCM< L >XWR    1QIsaa

In this case, the word "W" occurs three times in 1QIsaa, and only once in the BHSA. This means, that in the first two cases we cannot give these words an ETCBC lexeme. We can proceed by checking the lexeme "W" has in these cases in the dss module, which is "W:", and then find out with which lexeme "W:" corresponds in the BHSA most often. This is the BHSA lexeme "W", which can be given to the unmatched words "W".

This procedure works well in practice, but it is not infallible. In some cases the alignment is unfortunate, in other cases there is no one to one mapping between lexemes or the dss package has different definitions of what is a word. For instance, in the case of place names consisting of two words, the dss package treats them as distinct words, whereas the BHSA has one lexeme in general. To bring the resulting dataset to "ETCBC standard", more steps are needed. These can consist of additional automatic processing and/or manual cleaning.

The same approach is used for the feature part of speech. You can find the resulting dataset in the [github repository](https://github.com/ETCBC/DSS2ETCBC).

In [1]:
import collections
from pprint import pprint
import pandas as pd
import dill

The package biopython is used for aligning sequences

In [2]:
from Bio import pairwise2
from Bio.Seq import Seq

Now the dss package is loaded. The classes L, T and F, that are used here are renamed. In that case we can use them together

In [3]:
from tf.app import use
A = use('dss', hoist=globals())

# give the relevant classes for the DSS new names
Ldss = L
Tdss = T
Fdss = F

	connecting to online GitHub repo annotation/app-dss ... connected
Using TF-app in C:\Users\geitb/text-fabric-data/annotation/app-dss/code:
	rv0.6=#304d66fd7eab50bbe4de8505c24d8b3eca30b1f1 (latest release)
	connecting to online GitHub repo etcbc/dss ... connected
Using data in C:\Users\geitb/text-fabric-data/etcbc/dss/tf/0.6:
	rv0.6=#9b52e40a8a36391b60807357fa94343c510bdee0 (latest release)
	connecting to online GitHub repo etcbc/dss ... connected
Using data in C:\Users\geitb/text-fabric-data/etcbc/dss/parallels/tf/0.6:
	rv0.6=#9b52e40a8a36391b60807357fa94343c510bdee0 (latest release)
   |     0.00s No structure info in otext, the structure part of the T-API cannot be used


In [4]:
from tf.app import use
A = use('bhsa', hoist=globals())

	connecting to online GitHub repo annotation/app-bhsa ... connected
Using TF-app in C:\Users\geitb/text-fabric-data/annotation/app-bhsa/code:
	rv1.2=#5fdf1778d51d938bfe80b37b415e36618e50190c (latest release)
	connecting to online GitHub repo etcbc/bhsa ... connected
Using data in C:\Users\geitb/text-fabric-data/etcbc/bhsa/tf/c:
	rv1.6=#bac4a9f5a2bbdede96ba6caea45e762fe88f88c5 (latest release)
	connecting to online GitHub repo etcbc/phono ... connected
Using data in C:\Users\geitb/text-fabric-data/etcbc/phono/tf/c:
	r1.2 (latest release)
	connecting to online GitHub repo etcbc/parallels ... connected
Using data in C:\Users\geitb/text-fabric-data/etcbc/parallels/tf/c:
	r1.2 (latest release)
   |     0.01s No structure info in otext, the structure part of the T-API cannot be used


The dictionary book_dict_bhsa_dss provides a mapping between the booknames of the BHSA and dss packages. 

In [48]:
book_dict_bhsa_dss = {'Genesis':      'Gen',
             'Exodus':       'Ex',
             'Leviticus':    'Lev',
             'Numbers':      'Num',
             'Deuteronomy':  'Deut',
             'Joshua':       'Josh',
             'Judges':       'Judg',
             '1_Samuel':     '1Sam',
             '2_Samuel':     '2Sam',
             '1_Kings':      '1Kgs',
             '2_Kings':      '2Kgs',
             'Isaiah':       'Is',
             'Jeremiah':     'Jer',
             'Ezekiel':      'Ezek',
             'Hosea':        'Hos',
             'Joel':         'Joel',
             'Amos':         'Amos',
             'Obadiah':      'Obad',
             'Jonah':        'Jonah',
             'Micah':        'Mic',
             'Nahum':        'Nah',
             'Habakkuk':     'Hab',
             'Zephaniah':    'Zeph',
             'Haggai':       'Hag',
             'Zechariah':    'Zech',
             'Malachi':      'Mal',
             'Psalms':       'Ps',
             'Job':          'Job',
             'Proverbs':     'Prov',
             'Ruth':         'Ruth',
             'Song_of_songs':'Song',
             'Ecclesiastes': 'Eccl',
             'Lamentations': 'Lam',
             'Daniel':       'Dan',
             'Ezra':         'Ezra',
             '2_Chronicles': '2Chr'
            }

And the reversed way can be useful as well.

In [49]:
book_dict_dss_bhsa = {v: k for k, v in book_dict_bhsa_dss.items()}
print(book_dict_dss_bhsa)

{'Gen': 'Genesis', 'Ex': 'Exodus', 'Lev': 'Leviticus', 'Num': 'Numbers', 'Deut': 'Deuteronomy', 'Josh': 'Joshua', 'Judg': 'Judges', '1Sam': '1_Samuel', '2Sam': '2_Samuel', '1Kgs': '1_Kings', '2Kgs': '2_Kings', 'Is': 'Isaiah', 'Jer': 'Jeremiah', 'Ezek': 'Ezekiel', 'Hos': 'Hosea', 'Joel': 'Joel', 'Amos': 'Amos', 'Obad': 'Obadiah', 'Jonah': 'Jonah', 'Mic': 'Micah', 'Nah': 'Nahum', 'Hab': 'Habakkuk', 'Zeph': 'Zephaniah', 'Hag': 'Haggai', 'Zech': 'Zechariah', 'Mal': 'Malachi', 'Ps': 'Psalms', 'Job': 'Job', 'Prov': 'Proverbs', 'Ruth': 'Ruth', 'Song': 'Song_of_songs', 'Eccl': 'Ecclesiastes', 'Lam': 'Lamentations', 'Dan': 'Daniel', 'Ezra': 'Ezra', '2Chr': '2_Chronicles'}


We define some helper functions. align_verses takes two sequences das input and aligns them. It returns the aligned sequences.

In [50]:
def align_verses(bhsa_data, dss_data):
    
    seq_bhsa = ' '.join(bhsa_data).strip()
    seq_dss = ' '.join(dss_data).strip()
        
    seq1 = Seq(seq_bhsa) 
    seq2 = Seq(seq_dss)
    
    alignments = pairwise2.align.globalxx(seq1, seq2)
    
    bhsa_al = (alignments[0][0]).strip(' ')
    dss_al = (alignments[0][1]).strip(' ')
        
    return bhsa_al, dss_al

The function most_frequent takes a list with lexemes as input, and returns the most frequent lexeme, together with its frequency in the list.

In [51]:
from collections import Counter 
  
def most_frequent(lex_list): 
    occurrence_count = Counter(lex_list) 
    lex = occurrence_count.most_common(1)[0][0]
    count = occurrence_count.most_common(1)[0][1]
    return(lex, count)

In the function produce_value, the value of the POS or lexeme in the ETCBC format is retrieved.

In [52]:
def produce_value(key, chars_to_feat_etcbc, chars_to_feat_dss):
    
    # check for each consonant what the value of the feature is of the word of the corresponding consonant in the BHSA 
    if len(chars_to_feat_etcbc[(key[0], key[1], key[2])]) > 0:
        all_feat_etcbc = chars_to_feat_etcbc[(key[0], key[1], key[2])]
        
        # check for a word to which lexeme in the bhsa it corresponds with most of its characters
        feat_etcbc_proposed, count = most_frequent(all_feat_etcbc)
        
        # an etcbc-lexeme is assigned only to a word if more than half of its consonants
        # corresponds with a word in the BHSA    
        if len(list(word)) == 0:
            feat_etcbc = ''

        elif (count / len(list(word))) > 0.5:
            feat_etcbc = feat_etcbc_proposed

        else:
            feat_etcbc = ''
            
    else:
        feat_etcbc = ''
        
    if len(chars_to_feat_dss[key]) > 0:
        
        all_feat_dss = chars_to_feat_dss[key]
        feat_dss, count = most_frequent(all_feat_dss)
        
    else:
        feat_dss = ''
        
    return feat_dss, feat_etcbc

## Prepare scrolls


In the next cell the text and lexemes of the Great Isaiah scroll are extracted from the DSS package, and some minor manipulations are done with the text.

For every character in the text of the scroll 1QIsaa, we look up what the lexeme is of the word in which the character occurs. This information is saved in the dictionary lexemes_dss. The keys of this dict are the verse numbers of Isaiah. Each value is a list with the lexemes, one for each character in the verse.

Note that the data retrieved in the following cell consists partly of reconstructions of scrolls. Other features in the package, not discussed here, deal with which part of the text can be read on the scrolls and which part is reconstructed.

In [53]:
# In dss_data_dict, the text of each verse in the biblical scrolls is collected
dss_data_dict = collections.defaultdict(lambda: collections.defaultdict(list))
lexemes_dss = collections.defaultdict(lambda: collections.defaultdict(list))
pos_dss = collections.defaultdict(lambda: collections.defaultdict(list))
ids_dss = collections.defaultdict(lambda: collections.defaultdict(list))

for scr in Fdss.otype.s('scroll'):
    scroll_name = Tdss.scrollName(scr)
    
    words = Ldss.d(scr, 'word')
        
    for w in words:
            
        # exclude fragmentary data, these chapters start with 'f'
        chapter = Ldss.u(w, 'chapter')
        
        bo = Fdss.book.v(w) 
        
        if bo == None or bo not in book_dict_dss_bhsa:
            continue
        
        if (Fdss.chapter.v(w))[0] == 'f':
            continue
        
        # Do a bit of preprocessing
        if Fdss.glyphe.v(w) != None:
            
            lexeme = Fdss.glexe.v(w)
            glyphs = Fdss.glyphe.v(w)
            
            # dummy value, check what happens here
            if lexeme == None:
                #print(glyphs, scroll_name, int(Fdss.chapter.v(w)), int(Fdss.verse.v(w)))
                lexeme = 'XXX'
                
            # the consonant '#' is used for both 'C' and 'F'. We check in the lexeme
            # to which of the two alternatives it should be converted. This appproach is crude, 
            # but works well in practice. There is only one word with both F and C in the lexeme: >RTX##T> >AR:T.AX:CAF:T.:> in 4Q117
            if '#' in glyphs:  
                # hardcode the single word with both 'C' and 'F' in the lexeme.
                if glyphs == '>RTX##T>':
                    glyphs = '>RTXCFT>'
                    
                elif 'F' in lexeme:
                    glyphs = glyphs.replace('#', 'F')
                    
                # cases in wich 'C' occurs in lexeme or morphology
                else:                        
                    glyphs = glyphs.replace('#', 'C')                        
            
            # Some characters are removed or replaced, in the case of 'k', 'n', 'm', 'y', 'p', it concerns final consonants of words.
            glyphs = glyphs.replace(u'\xa0', u' ').replace("'", "").replace("k", "K").replace("n", "N").replace("m", "M").replace("y", "Y").replace("p", "P")   
                
            dss_book = Fdss.book.v(w)
            bhsa_book_name = book_dict_dss_bhsa[dss_book]
            
            # replace(' ', '') is needed for strange case in Exodus 13:16 with a space in the word
            dss_data_dict[(bhsa_book_name, int(Fdss.chapter.v(w)), int(Fdss.verse.v(w)))][scroll_name].append(glyphs.replace(' ', ''))
            
            ids_dss[bhsa_book_name, int(Fdss.chapter.v(w)), int(Fdss.verse.v(w))][scroll_name].append(w)
            
            # retrieve POS and lexeme of every character of every word in the scrolls and save in a dictionary
            for character in glyphs:   
                pos_dss[bhsa_book_name, int(Fdss.chapter.v(w)), int(Fdss.verse.v(w))][scroll_name].append(Fdss.sp.v(w))
                lexemes_dss[bhsa_book_name, int(Fdss.chapter.v(w)), int(Fdss.verse.v(w))][scroll_name].append(Fdss.glexe.v(w))


## Prepare BHSA

The same is done for all the characters in the text of Isaiah in the BHSA. Also, a list with the verses of Isaiah in the BHSA is made. Finally, for each verse, the consonantal structure of each word is collected per verse in the dictionary bhsa_data_dict.

In [54]:
all_verses = []
lexemes_bhsa = collections.defaultdict(list)
pos_bhsa = collections.defaultdict(list)

bhsa_data_dict = collections.defaultdict(list)

for w in F.otype.s('word'):
    
    # Remove words without consonantal representation in the text (elided he). 
    if F.g_cons.v(w) == '':
        continue
    
    bo, ch, ve = T.sectionFromNode(w)
    cl = L.u(w, "clause")[0]
    words_in_cl = L.d(cl, "word")
        
    # use feature g_cons for consonantal representation of words
    bhsa_data_dict[(bo, ch, ve)].append(F.g_cons.v(w))
        
    # loop over consonants and get lexeme of each consonant in a word
    for cons in F.g_cons.v(w):
        lexemes_bhsa[(bo, ch, ve)].append(F.lex.v(w)) 
        pos_bhsa[(bo, ch, ve)].append(F.sp.v(w))
        
    if (bo, ch, ve) not in all_verses:
        all_verses.append((bo, ch, ve))
    

## Align verses

In the following cell, the verses are aligned and characters are compared. 

In [55]:
chars_to_lexemes_etcbc = collections.defaultdict(list)
chars_to_lexemes_dss = collections.defaultdict(list)

chars_to_pos_etcbc = collections.defaultdict(list)
chars_to_pos_dss = collections.defaultdict(list)
chars_per_word =  collections.defaultdict(list)

all_verses = list(set(all_verses))

# loop over verses in BHSA
for verse in all_verses:
    
    # check if verse occurs in the dss package
    if verse in dss_data_dict:
        
        scrolls = (dss_data_dict[verse]).keys()
        
        for scroll in scrolls:
            
            # get the text of the verse
            bhsa_data = bhsa_data_dict[verse]
            dss_data = dss_data_dict[verse][scroll]
            
            # all pairs of verses in the BHSA and scrolls are aligned
            bhsa_al, dss_al = align_verses(bhsa_data, dss_data)
             
            print(verse)
            print('BHSA')
            print(bhsa_al)
            print(scroll)
            print(dss_al)
            print(' ')
        
            # some indexes are initialized, these keep track of how many consonants have been observed 
            # in both aligned sequences
            ind_dss = 0
            ind_bhsa = 0
        
            dss_word_ind = 0
        
            # loop over all characters in the BHSA verse
            for pos in range(len(bhsa_al)):
            
                # for each character in the BHSA sequence, it is cheched what the character is in the DSS sequence.
                # Now, a number of scenarios are defined. Most scenarios are not so exciting, e.g.
                # if the character is a space in both sequences, then move further
                if bhsa_al[pos] == ' ' and dss_al[pos] == ' ':
                    
                    dss_word_ind += 1
            
                elif bhsa_al[pos] == '-' and dss_al[pos] == ' ':
                    
                    dss_word_ind += 1
                
                elif bhsa_al[pos] == ' ' and dss_al[pos] == '-':
                    
                    chars_per_word[(scroll, verse, dss_word_ind)].append(dss_al[pos])
                               
                else:
                    if bhsa_al[pos] == '-':
                        
                        chars_per_word[(scroll, verse, dss_word_ind)].append(dss_al[pos])
                        chars_to_lexemes_dss[(scroll, verse, dss_word_ind)].append(lexemes_dss[verse][scroll][ind_dss])
                        chars_to_pos_dss[(scroll, verse, dss_word_ind)].append(pos_dss[verse][scroll][ind_dss])
                        
                        ind_dss += 1
                    
                    elif dss_al[pos] == '-':
                        
                        chars_per_word[(scroll, verse, dss_word_ind)].append(dss_al[pos])
                        
                        ind_bhsa += 1
                    
                    # Now the real matching is done
                    # For a matching consonant, it is checked in the dicts to which lexeme it corresponds
                    else:                        
                        
                        chars_to_lexemes_etcbc[(scroll, verse, dss_word_ind)].append(lexemes_bhsa[verse][ind_bhsa])
                        chars_to_pos_etcbc[(scroll, verse, dss_word_ind)].append(pos_bhsa[verse][ind_bhsa])
                        
                        chars_to_lexemes_dss[(scroll, verse, dss_word_ind)].append(lexemes_dss[verse][scroll][ind_dss])
                        chars_to_pos_dss[(scroll, verse, dss_word_ind)].append(pos_dss[verse][scroll][ind_dss])
                        chars_per_word[(scroll, verse, dss_word_ind)].append(dss_al[pos])
                    
                        ind_dss += 1
                        ind_bhsa += 1               

('Genesis', 45, 18)
BHSA
W QXW >T >BJKM W >T BTJKM W B>W >LJ W >TNH LKM >T VWB >RY MYRJM W >KLW >T XLB H >RY
4Q9
W QXW >T >BJKM W >T BTJKM W B>W >LJ W >TNH LKM >T VWB >RY MYRJM W >KLW >T XLB H >RY
 
('Psalms', 119, 4)
BHSA
>TH YWJTH PQ-DJK- L CM-R M->D-
11Q5
>T- YWJTH PQWDJKH L CMWR MW>DH
 
('Numbers', 23, 21)
BHSA
L-> H-BJV >-WN B J<Q-B W L-> R>H <ML B JFR>L JHWH >L-HJW <MW W TRW<T MLK BW
4Q27
LW> ->BJV -<WN B J<QWB W LW> R>H <ML B JFR>L JHWH >LWHJW <MW W TRW<T MLK BW
 
('Micah', 2, 10)
BHSA
QWMW W LKW KJ L> Z>T H MNWXH B <BWR VM>H TXBL W XBL NMRY
Mur88
QWMW W LKW KJ L> Z>T H MNWXH B <BWR VM>H TXBL W XBL NMRY
 
('Ezekiel', 41, 3)
BHSA
W B> L PNJMH W JMD >JL H PTX CTJM >MWT W H PTX CC >MWT W RXB H PTX CB< >MWT
4Q73
W B> L PNJMH W JMD >JL H PTX CTJM >MWT W H PTX CC >MWT W RXB H PTX CB< >MWT
 
('Deuteronomy', 27, 10)
BHSA
W CM<T B QWL JHWH >LHJK W <FJT >T MYWTW W >T XQJW >CR >NKJ MYWK H JWM
4Q33
W CM<T B QWL JHWH >LHJK W <FJT >T MYWTW W >T XQ-------------------JW-
 
('Isaiah', 12, 2)
BHS

('2_Samuel', 12, 31)
BHSA
W >T H <M >CR BH HWYJ> W JFM- B MGRH W B XRYJ H BRZL W B MGZRT H BRZL W H<BJR >WTM B MLK-N W KN J<FH L K-L <RJ BNJ <MWN W JCB DW-D W K-L H <M JRWCL-M
4Q51
W >T H <M >CR BH HWYJ> W JF-R B MGRH W B XRY- H BRZL W B MGZR--H----- W H<BJR >WTM B ML-BN W KN J<FH L KWL <RJ BNJ <MWN W JCB DWJD W KWL H <M JRWCLJM
 
('Leviticus', 9, 15)
BHSA
W JQRB >T QRBN H <M W JQX >T F<JR H XV>T >CR L <M W JCXVHW W JXV>HW K R>CWN
Mas1b
W JQRB >T QRBN H <M W JQX >T F<JR H XV>T >CR L <M W JCXVHW W JXV>HW K R>CWN
 
('Deuteronomy', 8, 20)
BHSA
K GWJM >CR JHWH M>BJD M PNJKM KN T>BDWN <QB L> TCM<WN B QWL JHWH >LHJKM
5Q1
K GWJM >CR JHWH M>BJD M PNJKM KN T>BDWN <QB L> TCM<WN B QWL JHWH >LHJKM
 
('Isaiah', 33, 15)
BHSA
H-L-K YDQWT W -DBR MJCRJM M>S B BY< M<CQWT N<R KPJW M TMK B CX-D >-VM >-ZN-W M CM-< DMJM W -<YM <JNJW M R>WT B R<
1Qisaa
HWLWK YDQWT W JDBR MJCRJM M>S B BY< M<CQWT N<R KP-W M TMK B CXWD >WVM >WZNJW M CMW< DMJM-- J<YM <JNJW M R>WT B R<
 
('Psalms', 33, 9)
BHSA
KJ HW> >MR W JHJ HW

('Deuteronomy', 5, 24)
BHSA
W T>MRW HN HR>NW JHWH >LHJNW >T KB-DW W >T G-DLW W >T Q-LW CM<NW M TWK H >C H JWM H ZH R>JNW KJ JDBR >LHJM--- >T H >DM W XJ
4Q137
W T>MRW HN HR>NW JHWH >LHJNW >T KBWDW W >T GWDLW W >T QWLW CM<NW M TWK H >C H JWM H ZH R>JNW KJ JDBR ---J-HWH >T H >DM W XJ
 
('Deuteronomy', 5, 24)
BHSA
W T>MRW HN- HR>NW JHWH >LHJNW >T KBDW W >T GDLW W >T QLW CM<NW M TWK H >C H JWM H ZH R>JNW KJ JDBR >LHJM >T H >DM W XJ
4Q139
W T>MRW HNH HR>NW JHWH >LHJNW >T KBDW W >T GDLW W >T QLW CM<NW M TWK H >C H JWM H ZH R>JNW KJ JDBR--------------------
 
('Deuteronomy', 5, 24)
BHSA
W T>MRW HN HR>NW JHWH >LHJNW >T KB-DW W >T GDLW W >T Q-LW CM<NW M TWK H >C H JWM H ZH R>JNW KJ JDBR >LHJM >T H >DM W XJ
Xq2
W T>MRW HN HR>NW JHWH >LHJNW >T KBWDW W >T GDLW W >T QWLW CM<NW M TWK H >C H JWM H ZH R>JNW KJ JDBR >LHJM >T H >DM W XJ
 
('Exodus', 27, 12)
BHSA
W RXB H XYR L P>T JM QL<JM XMCJM >MH <MDJHM <FRH W >DNJHM <FRH-----
4Q11
W RXB H XYR L P>T JM QL<JM XMCJM >MH <MDJHM <FRH-- ----HM <FRH NXCT
 
(

('Judges', 4, 9)
BHSA
W T>MR HLK >LK <MK >PS KJ L> THJH TP>RTK <L H DRK >CR >TH HWLK KJ B JD >CH JMKR JHWH >T SJSR> W TQM DBWRH W TLK <M BRQ QDCH
Xjudges
W T>MR HLK >LK <MK >PS KJ L> THJH TP>RTK <------------------L------------------ ---H--------------- D--R------K------------
 
('2_Samuel', 20, 21)
BHSA
L> KN H DBR KJ >JC M HR >PRJM CB< BN BKRJ CMW NF> JDW B-- --MLK B DW-D TNW --->TW L BDW W >LKH M <L H <JR W T>MR H >CH >L JW>B HNH R>CW MCLK >LJK B<D H XWMH
4Q51
L> KN H DBR KJ >JC M HR >PRJM CB< BN BKRJ---- NF> JDW -<L H MLK-- DWJD TNW LJ >TW L BDW W >LKH M <L H <JR W T>MR H >CH >L JW>B HNH R>CW MCLK >LJK B<D H XWMH
 
('Ezekiel', 11, 3)
BHSA
H >MRJM L> B QRWB BNWT BTJM HJ> H SJR W >NXNW H BFR
4Q73
H >MRJM L> B QRWB BNWT BTJM HJ> H SJR W >NXNW H BFR
 
('Isaiah', 36, 16)
BHSA
>L TCM<W >L X-ZQJHW KJ- K-H >MR H MLK >CWR <FW >TJ BRKH W Y>W >LJ W >K-LW >JC ---GPNW W >JC T>---NTW W CTW >JC MJ BWRW
1Qisaa
>L TCM<W >L XWZQJH- KJ> KWH >MR-- MLK >CWR <FW >TJ BRKH W Y>W >LJ W >KWLW >JC >T GPNW W 

('Genesis', 34, 21)
BHSA
H >NCJM H >LH CLMJM HM >TNW W JCBW B >RY W JSXRW >TH W H >RY HNH RXBT JDJM L PNJHM >T BNTM NQX LNW L NCJM W >T BNTJNW NTN LHM
4Q1
H >NCJM H >LH CLMJM HM >TNW W JCBW B >RY W JSXRW >TH W H >RY HNH RXBT JDJM L PNJHM >T BNTM NQX LNW L NC-----------J---------M
 
('Psalms', 122, 1)
BHSA
CJR H M<LWT L DW-D FMXTJ B >-MRJM LJ BJT JHWH NLK
11Q5
CJR H M<LWT L DWJD FMXTJ B >WMRJM LJ BJT JHWH NLK
 
('Psalms', 25, 8)
BHSA
VWB W JCR JHWH <L KN JWRH XV>JM B DRK
4Q83
VWB W JCR JHWH <L KN JWRH XV>JM B DRK
 
('Leviticus', 10, 19)
BHSA
W JDBR >HRN >L MCH HN H JWM HQRJBW >T XV>TM W >T <LTM L PNJ JHWH W TQR>NH >TJ K >LH W >KLTJ XV>T H JWM H JJVB B <JNJ JHWH
Mas1b
W JDBR >HRN >L MCH HN H JWM HQRJBW >T XV>TM W >T <LTM L PNJ JHWH W TQR>NH >TJ K >LH W >KLTJ XV>T H JWM H JJVB B <JNJ JHWH
 
('Exodus', 14, 22)
BHSA
W JB>W BNJ JFR>L B TWK H JM B JBCH W H MJM LHM X-MH M JMJNM W M FM>LM
4Q11
W JB>W BNJ JFR>L B TWK H JM B JBCH W H MJM LHM XWMH M JMJNM W M FM>LM
 
('Exodus', 14, 22)
BHSA
W JB>W

...

('Leviticus', 20, 20)
BHSA
W >JC >CR JCKB >T DDTW <RWT DDW GLH XV>M JF>W <RJRJM JMTW
1Q3
------------------------------------XV>M JF>W <RJRJM JMTW
 
('2_Samuel', 18, 10)
BHSA
W JR> >JC >XD W JGD L JW>B W J>MR HNH R>JTJ >T >BCL-M TLWJ B >LH
4Q51
W JR> >JC---- W JGD L JW>B W J>MR HNH R>JTJ >T >BCLWM TLWJ B >LH
 
('Numbers', 26, 16)
BHSA
L >ZNJ MCPXT H >ZNJ L <R-J MCPXT H <R-J
4Q27
L >ZNJ MCPXT H >ZNJ L <-DJ MCPXT H <-DJ
 
('Job', 37, 5)
BHSA
JR<M >-L B QWLW NPL>WT <FH GDLWT W L> ND<
4Q99
JR<M -<L B QWLW NPL>WT <FH GDLWT W L> ND<
 
('Psalms', 94, 4)
BHSA
JBJ<W JDBRW <TQ JT>MRW KL P<LJ >WN
4Q84
JBJ<W JDBRW <TQ JT>MRW KL P<LJ >WN
 
('Zephaniah', 3, 20)
BHSA
B <T H HJ> >BJ> >TKM W B <T QBYJ >TKM KJ >TN >TKM L CM W L THLH B KL <MJ H >RY B CWBJ >T CBWTJKM L <JNJKM >MR JHWH
4Q77
B <T H HJ> >BJ> >TKM W B <T QBYJ >TKM KJ >TN >TKM L CM W L THLH B KL <MJ H >RY B CWBJ >T CBWTJKM L <JNJKM >MR JHWH
 
('Zephaniah', 3, 20)
BHSA
B <T H HJ> >BJ> >TKM W B <T QBYJ >TKM KJ >TN >TKM L CM W L THLH B KL <MJ H >

('Genesis', 5, 13)
BHSA
W JXJ QJNN >XRJ HWLJDW >T MHLL>L >RB<JM CNH W CMNH M>WT CNH W JWLD BNJM W BNWT
4Q2
------QJNN >XRJ HWLJDW >T MHLL>L >RB<JM CNH W CMNH M>WT CNH-------------------
 
('Psalms', 31, 21)
BHSA
TSTJRM B STR PNJK M RKSJ >JC TYPNM B SKH M RJB LCNWT
5/6hev1b
TSTJRM B STR PNJK M RKSJ >JC TYPNM B SKH M RJB LCNWT
 
('1_Samuel', 22, 9)
BHSA
W J<N D>G H >DMJ W HW> NYB <L <BDJ C>WL W J>MR R>JTJ >T BN JCJ B> NBH >L >X-JMLK BN >XVWB
4Q52
W J<N D>G H >DMJ-- H-- NYB <L <BDJ C>WL W J>MR R>JTJ >T BN JCJ B> NBH >L >-BJMLK---------
 
('Micah', 5, 1)
BHSA
W >TH BJT_-LXM >PRTH Y<JR L HJWT B >LPJ JHWDH MMK LJ ---JY> L HJWT MWCL B JFR>L W MWY>TJW M QDM M JMJ <WLM
4Q81
W >TH BJT- LXM >PRTH Y<JR L HJWT B >LPJ JHWDH MMK LJ L> JY> L HJWT MWCL B JFR>L W MWY>TJW M QDM M JMJ <WLM
 
('Micah', 5, 1)
BHSA
W >TH BJT_-LXM >PRTH Y<JR L HJWT B >LPJ JHWDH MMK LJ JY> L HJWT MWCL B JFR>L W MWY>TJW M QDM M JMJ <WLM
Mur88
W >TH BJT- LXM >PRTH Y<JR L HJWT B >LPJ JHWDH MMK LJ JY> L HJWT MWCL B JFR>L W MWY>TJW

('Isaiah', 57, 8)
BHSA
W >XR H DLT W H MZWZH FMT ZKRWNK KJ M >TJ GLJT W T<LJ HRXBT MCKBK W TKRT LK MHM >HBT MCKBM JD XZJT
4Q62a
W >XR H DLT W H MZWZH FMT ZKRWNK KJ M >TJ GLJT W T<LJ HRXBT MCKBK W TKRT LK MHM >H------B--------T
 
('Genesis', 18, 23)
BHSA
W JGC >BRHM W J>MR H >P TSPH YDJQ <M RC<
8Q1
W JGC >BRHM W J>MR H >P TSPH YDJQ <M RC<
 
('Deuteronomy', 32, 6)
BHSA
H L JHWH TGMLW Z>T <M NBL W L> XKM H LW> HW> >BJK QNK HW> <FK W JKNNK
4Q45
-------------------------------XKM H LW> HW> >BJK QNK HW> <FK W JKNNK
 
('Habakkuk', 1, 4)
BHSA
<L KN TPWG TWRH W L> JY> L NYX MCPV KJ RC< MKTJR >T H YDJQ <L KN JY> MCPV M<QL
Mur88
<L KN TPWG TWRH W L> JY> L NYX MCPV KJ RC< MKTJR >T H YDJQ <L KN JY> MCPV M<QL
 
('2_Samuel', 15, 10)
BHSA
W JCLX >BCLWM M--RG--LJM B K-L CBVJ JFR>L L >M-R K C-M<KM >T QWL H C-PR W >MRTM MLK >BCLWM B XBRWN
4Q53
W JCLX >BCLWM M JR-WCL-M B KWL CBVJ JFR>L L >MWR K CWM<KM >T QWL H CWPR W >MRTM MLK >BCLWM B XBRWN
 
('Psalms', 7, 13)
BHSA
>M L> JCWB XRBW JLVWC QCTW DRK W JKWNNH

('Deuteronomy', 11, 8)
BHSA
W CMRTM- >T K-L H MYWH >CR >NKJ MYWK H JWM LM<N TXZQW W B>TM W JRCTM >T H >RY >CR >TM <BRJM ----------CMH L RCTH
4Q128
W CMRTMH >T KWL H MYWH >CR >NKJ MYWK H JWM LM<N TXZQW W B>TM W JRCTM >T H >RY >CR >TM <BRJM >T H JRDN CMH L RCTH
 
('Deuteronomy', 11, 8)
BHSA
W CMRTM- >T K-L H MYWH >CR >N-KJ MY-WK- H JWM LM<N TXZQW W -B>-TM- W -------JRCTM- >T H >RY >CR >TM- <-BRJM ----------CMH L RCTH
4Q138
W CMRTMH >T KWL H MYWH >CR >NWKJ MY WKH H JWM LM<N TXZQW W <B-RTMH W BTMH W JRCTMH >T H >RY >CR >TMH <WBRJM >T H JRDN CMH L RCTH
 
('Deuteronomy', 11, 8)
BHSA
W CMRTM >T KL H MYWH >CR >NKJ MYWK H JWM LM<N TXZQ-W W --B>TM W JRCTM >T-- H- >RY >CR >TM <BR-JM CMH L RCTH
8Q3
-----------------------------------------LM<N TX--JW W JVB----W J---M---JM -B >RY >CR >TM -B->JM CM- L RCTH
 
('Deuteronomy', 11, 8)
BHSA
W CMRTM >T KL H ---MY-W-H ------->CR >NKJ MYW----K- H JWM LM<N TXZQW W -B------->TM W JRCTM >T H >RY >CR >TM <BRJM CMH L RCTH
8Q4
W CMRTM >T KL H XQJM- W H MCPVJM >CR

('2_Samuel', 23, 9)
BHSA
W >XRW >L<ZR BN DDJ BN >X-XJ B CLCH GBRJM <M DW-D B XRPM B PLCTJM N>SPW CM L MLXMH W J<LW >JC JFR>L
1Q7
------->L<ZR------- BN >XWXJ B CLCH GBRJM <M DWJD B XRPM B PLCTJM N>SPW CM L MLXMH W J<LW >JC JFR>L
 
('Psalms', 69, 17)
BHSA
<NNJ JHWH KJ VWB XSDK- K RB RXMJK- PNH >LJ
4Q83
<NN--J--- K- VWB XSDKH K RB RXMJKH PNH >LJ
 
('Exodus', 28, 8)
BHSA
W XCB >PDTW >CR <LJW K M<FHW MMNW JHJH ZHB TKLT W >RGMN W TWL<T CNJ W CC MCZR
4Q22
------------>CR <LJW K M<FHW MMNW JHJH ZHB TKLT W >RGMN W TWL<T CNJ W CC MCZR
 
('Isaiah', 41, 7)
BHSA
W JXZQ XRC >T Y-RP MXLJQ P-VJC >T H-WLM P<M -->MR L DBQ VWB HW>- W JXZQHW B MSMRJM L-> JMWV
1Qisaa
W JXZQ XRC >T YWRP MXLJQ PLVJC >T ->WLM P<M JW>MR L DBQ VWB HW>H W JXZQHW B MSMRJM LW> JMWV
 
('Isaiah', 41, 7)
BHSA
W JXZQ XRC >T YRP MXLJQ PVJC >T HWLM P<M >-MR L DBQ VWB HW> W JXZQHW B MSMRJM L> JMWV
1Q8
W JXZQ XRC >T YRP MXLJQ PVJC >T HWLM P<M >WMR L DBQ VWB HW> W JXZQHW B MSMRJM L> JMWV
 
('Isaiah', 66, 7)
BHSA
B VRM TXJL JLDH B VRM JBW>

## Postprocess data

Lexemes and parts of speech are collected and stored in lists, these are converted later to a pandas dataframe.

The distionary mapping_dict shows which lexemes in the dss package correspond with their new BHSA alternatives.

In [76]:
tf_word_id = [] # tf index
scrolls = [] # scroll code
books = [] # biblical book name
chapters = [] # chapter number
verses = [] # verse number
words_dss = [] # consonantal representation of word on scroll
lexs_dss = [] # lexeme in dss package
lexs_etcbc = [] # corresponding etcbc lexeme
poss_dss = [] # POS in dss package
poss_etcbc = [] # corresponding etcbc POS

mapping_dict = collections.defaultdict(lambda: collections.defaultdict(list))

# loop over all words in the dss, and in each word over all consonants
for key in chars_per_word.keys():
    
    tf_word_id.append(ids_dss[key[1]][key[0]][key[2]])

    word = (''.join(chars_per_word[key])).replace("-", "")
    
    lexeme_dss, lexeme_etcbc = produce_value(key, chars_to_lexemes_etcbc, chars_to_lexemes_dss)
    pos_dss, pos_etcbc = produce_value(key, chars_to_pos_etcbc, chars_to_pos_dss)
    
    if lexeme_dss != '':
        mapping_dict[lexeme_dss][(key[0], key[1])].append(lexeme_etcbc)
    
    # collect info in lists
    scrolls.append(key[0])
    books.append(key[1][0])
    chapters.append(key[1][1])
    verses.append(key[1][2])
    words_dss.append(word)
    lexs_dss.append(lexeme_dss)
    lexs_etcbc.append(lexeme_etcbc)
    poss_dss.append(pos_dss)
    poss_etcbc.append(pos_etcbc)
    

In the following two cells, some empty cells are filled, using the second part of the procedure above.

In [77]:
# the list second remembers which cases have been given a lexeme this way

second = []

for index, lex in enumerate(lexs_etcbc):
    if lex == '' and Fdss.lang.v(tf_word_id[index]) != 'a': # exclude aramaic, some strange cases
        if lexs_dss[index] != '':
        
            all_candidates_lists = list((mapping_dict[lexs_dss[index]]).values())
            candidates_list = [item for sublist in all_candidates_lists for item in sublist]
        
            best_cand, count = most_frequent(candidates_list)

            lexs_etcbc[index] = best_cand
            second.append('x')
        else:
            second.append('')
    else:
        second.append('')


In [78]:
# Check suspect cases:

# 1. Cases of lexemes occurring with more than one pos
# 2. Cases where the pos on basis of alignment does not coincide with pos on basis of ETCBC (close to 1.)
# 3. Lexemes with a consonantal representation that does not occur in the BHSA


In [74]:
mapping_lex_pos = collections.defaultdict(list)
mapping_id_pos = collections.defaultdict(lambda: collections.defaultdict(list))

for index, lex in enumerate(lexs_etcbc):
    
    if lex == "" or poss_etcbc[index] == "":
        continue
        
    else:
        mapping_lex_pos[lex].append(poss_etcbc[index])
        mapping_id_pos[lex][poss_etcbc[index]].append(tf_word_id[index])

In [60]:
mapping_id_pos

defaultdict(<function __main__.<lambda>()>,
            {'W': defaultdict(list,
                         {'conj': [1941548,
                           1941552,
                           1941555,
                           1941558,
                           1941565,
                           1974002,
                           1974011,
                           2095040,
                           2095051,
                           2036119,
                           2036123,
                           2036130,
                           2036135,
                           1984939,
                           1984945,
                           1984949,
                           1899391,
                           1899396,
                           2016824,
                           2016829,
                           2016833,
                           2026076,
                           2026081,
                           2026085,
                           2004042,
            

In [61]:
# to check: some lexemes have more than one pos, that needs to be corrected somehow

for key in mapping_lex_pos.keys():
    if len(set(mapping_lex_pos[key])) > 1:
        print(key, collections.Counter(mapping_lex_pos[key]))

>B/ Counter({'subs': 418, 'verb': 1, 'prep': 1})
>L Counter({'prep': 2283, 'nega': 3, 'nmpr': 1, 'subs': 1})
NTN[ Counter({'verb': 856, 'subs': 1})
>RY/ Counter({'subs': 1565, 'verb': 1})
MYRJM/ Counter({'nmpr': 618, 'subs': 1})
H Counter({'art': 9611, 'inrg': 5})
L> Counter({'nega': 2983, 'verb': 1, 'prep': 1})
B Counter({'prep': 7559, 'subs': 1})
R>H[ Counter({'verb': 680, 'subs': 1})
JHWH/ Counter({'nmpr': 4114, 'subs': 1})
MLK/ Counter({'subs': 772, 'prep': 1})
KJ Counter({'conj': 2441, 'subs': 3})
HJH[ Counter({'verb': 1817, 'subs': 2})
DWD==/ Counter({'nmpr': 315, 'subs': 1})
<L Counter({'prep': 2806, 'subs': 3})
LB/ Counter({'subs': 253, 'verb': 1})
MN Counter({'prep': 3725, 'subs': 1})
KL/ Counter({'subs': 2667, 'nmpr': 1})
>MR[ Counter({'verb': 2305, 'subs': 1})
HW> Counter({'prps': 669, 'verb': 1})
HN Counter({'intj': 81, 'conj': 4})
BL<M/ Counter({'nmpr': 33, 'subs': 1})
QR>[ Counter({'verb': 456, 'nmpr': 1})
>DNJ/ Counter({'nmpr': 176, 'subs': 1})
>T= Counter({'prps': 16, '

In [62]:
mapping_id_pos['H']['inrg'] # all cases in aramaic daniel: distinguish between aramaic and hebrew

[1929649, 2061573, 2060092, 2058203, 2060378]

In [63]:
mapping_id_pos['<ZQH/']['subs'] # <ZQH/ is nmpr in Hebrew, subs in aram

[2060289, 2060292]

In [64]:
mapping_id_pos['BL/']['subs'] # aram Daniel

[2060190]

In [65]:
mapping_id_pos['XD/']['subs'] # XD/ is subs in aram, adjv in Hebrew

[2061844, 2058334, 2059207, 2060277, 2062493, 2060457, 2058409, 2062482]

In [66]:
mapping_id_pos['HJH[']['subs'] # mistakes!

[2027218, 2065760]

In [67]:
mapping_id_pos['QR>[']['nmpr']

[2099910]

In [68]:
# ad. 3

lex2cons = collections.defaultdict(set)
for w in F.otype.s('word'):
    lex2cons[F.lex.v(w)].add(F.g_cons.v(w))
n = 0
for ind in range(len(lexs_etcbc)):
    lex_etcbc = lexs_etcbc[ind]
    cons = words_dss[ind]
    
    if cons not in lex2cons[lex_etcbc] and lex_etcbc != '':
        n += 1
        print(tf_word_id[ind], cons, lex_etcbc)
        
print(n)

2084083 PQWDJKH PQWDJM/
2084086 MW>DH M>D/
1973999 <WN >WN=/
1974009 >LWHJW >LHJM/
1899394 KJ> KJ
1899395 <WZJ <Z=/
1899400 HJH> HJH[
2004058 JTLWM TLH[
2004067 MPJBCT >JC_BCT/
2010090 BJT BJT_LXM/
2010091 LXM BJT_LXM/
2011713 XY XYJ=/
1933635 FMLTJK FMLH/
1909931 HNH HN
1909932 >TMH >TM
1909936 PW<LKMH P<L/
1909939 BKMH B
1922343 >PS >P</
1918652 R>JTMH R>H[
1918655 LBKMH LB/
1918657 <YMWTJKMH <YM/
1940696 >DMH >DM/
2084353 <WDWNJ <WD[
2084354 TWRTKH TWRH/
1974037 RW>C R>C/
2046380 L LKN
2046381 KN LKN
2046398 YW>RWTJHM YW>R/
2094911 L LKN
2094912 KN LKN
2022116 XWKMT XKMH/
1981023 Z>T ZH
1974174 NVWJM NVH[
1974180 >WHLJM >HL==/
1974181 NVH NV<[
2086586 TQW< TQ</
2107325 HLLHW HLL[
2107329 HLLHW HLL[
2105889 HSRWTJ SWR[
2087574 XWCK XCK/
2087577 SWKTW SKH/
2087578 XCKWT XCKH/
1909803 LCWNMH LCWN/
1909805 YMH YM>=/
1909813 ><ZWBM <ZB[
1918724 >WKLJ >KL[
1918727 XWZJR XZJR/
1918730 CQWY CQY/
1918735 >MR N>M/
2006261 JFR FJM[
2006266 XRY XRJY/
2006271 MGZRH MGZRH/
1906369 HWLWK HLK[
1906

2020750 KJ> KJ
1974597 QWRX QRX==/
1974607 QWRX QRX==/
1974616 QVWRT QVRT/
2060177 > MLK/
2060181 > MLH/
2060192 ZBWTH JZB[
2060197 > CMC/
2002731 >LWHJM >LHJM/
1894760 L LXMJ/
1894762 L GLJT/
2090202 BJT BJT_>L/
2090203 >L BJT_>L/
2055793 KLWTJH KLH/
1910857 >NWKJ >NKJ
1910858 >NWKJ >NKJ
1910859 HW>H HW>
1910860 MWXH MXH[
1910861 PC<KH PC</
1910864 XV>TJKH XV>T/
1910866 >ZKWR ZKR[
1955856 >HRWN >HRN/
1903389 HCXH CXX[
1920681 M XWMH/
2021597 XWMWTJKH XWMH/
2007040 KLWTW KLH[
2007064 M>WD M>D/
1906909 KWCLWT KCL[
1974465 MWCH MCH=/
1974469 >HRWN >HRN/
1974471 KWHN KHN/
1974472 >WTMH >T
2083308 XWQ XQ/
2037299 JP> JPW/
1953548 XRVWMJM XRVM/
2067496 K JCB[
2070051 CNNTMH CNN=[
2070053 BNJKH BN/
2070055 DBRTH DBR[
2070056 BMH B
2070058 CBTKH JCB[
2070063 L HLK[
2070064 KTKH HLK[
2070069 CKBKH CKB[
2070072 QWMKH QWM[
2102693 CNNT CNN=[
1944921 M VB<T/
1958585 QRJCJM QRC/
2084977 TWRTKH TWRH/
2086770 TWRTKH TWRH/
2005329 JKRWT KRT[
1993848 H >LMNH/
1903236 XWRB XRB=/
1903242 XWRB XRB=/
1906

2004540 NWDN NKWN=/
2004549 >LWHJM >LHJM/
2064950 JBJ>KH BW>[
2064962 >BWTJKH >B/
2065298 >BWTK >B/
2065911 JBJ>KH BW>[
2071774 > >CR
2071775 CR >CR
2102532 >BWTK >B/
1915861 >GWDWT >GDH/
1915862 MVH MWVH/
1915866 XWPCJJM XPCJ/
1925455 XRYBT XRYB/
1925459 MVH MWVH/
1925461 RYYJM RYY[
1925465 MVH MWVH/
2063307 HW>H HW>
2063308 THLTKH THLH/
2063312 >LWHJKH >LHJM/
2063315 >TKH >T==
2068408 HW>H HW>
2068409 THLTKH THLH/
2068411 HW>H HW>
2068413 >LWHJKH >LHJM/
2068416 >TKH >T==
2068419 GDWLWT GDWL/
2068428 <JNJKH <JN/
2076991 NWR>W JR>[
2078266 >WTK >T==
1904750 JW>MR >MR[
1904767 RXWQ RXQ[
1908999 JW>MR >MR[
1909000 JXWZQJH XZQJHW/
1909002 JC<JH JC<JHW/
1909007 DBRTH DBR[
1909009 JW>MR >MR[
1909010 KJ> KJ
2009921 GWJJM GWJ/
1895651 YWRJM YWR/
1895667 <RWY <RY[
2083425 CWMRKH CMR[
2083427 YLKH YL/
2083430 JMJNKH JMJN/
1932075 QVWN QVN/
1894193 HMH HNH
2051195 >WJBJKH >JB[
2051200 MCJXKH MCJX/
2042513 B<L B<L_P<WR/
2042514 P<WR B<L_P<WR/
1913453 J<ZWR <ZR[
1913467 KJ> KJ
2003513 PTWTK PTH[
1

2013453 JJJJ JHWH/
2013458 JJJJ JHWH/
1913109 HNH HN
1913112 XWQWTJK XQQ[
2063719 FDKH FDH/
2070343 FB<TH FB<[
1904067 KWHN KHN/
1904069 NBJ NBJ>/
2021740 KWHN KHN/
1908478 JC<JH JC<JHW/
1895193 HJKH >JKH
1975932 MVJ MVH/
1975935 MVJ MVH/
2048271 <LJKH <L
2050660 <YBTM <YBH/
1915388 >TMH >TM
1915389 QRWBW QRB[
1915396 TZNW ZNH[
2007669 HWGD NGD[
2007674 QWCRJM QCR[
1890430 L >LHJM/
1913271 KJ> KJ
1913272 KWH KH
1913278 JLQX LQX[
1913280 CWBJ CBH[
1913285 RWBJK JRJB/
1913286 >NWKJ >NKJ
1913291 >NWKJ >NKJ
1988410 L >HL/
2063514 QWRX QRX==/
2068577 >BJRWM >BJRM/
2068579 >LJB >LJ>B/
2068592 BTJHMH BJT/
2068595 >HLJHMH >HL/
2068603 QWRX QRX==/
2068611 RGLJHMH RGL/
2077668 DT DTN=/
2077673 >LJB >LJ>B/
2077675 RBN R>WBN/
2077687 BTJHKM BJT/
1904197 L LKN
1904198 KN LKN
2021869 L LKN
2021870 KN LKN
1908681 LW> L
1908683 HJ>H HJH[
1908685 LJ> L
1908686 >DWDH DDH[
1908690 MWR MR/
1908691 NPCJ> NPC/
1895329 NWBLT NBL[
1976123 MWCH MCH=/
1976127 KWHN KHN/
1976133 MWCH MCH=/
2084144 GRCH GRS[
20841

1904778 L LKN
1904779 KN LKN
1904781 >NWKJ >NKJ
1904792 PLH PL>/
1904799 NBWNJW BJN[
1895645 JXLWPW XLP[
1932081 JW>MR >MR[
1932082 >LWHJMH >L
1932083 KWH KH
1932089 CLXTMH CLX[
1932094 TXNWTJKMH TXNH/
1913441 MVLJM MRV[
1913444 HSJRWTJ STR[
1913448 RWQ RQ/
1904601 GW>JM GWJ/
1904603 YWB>JM YB>[
1904605 >RW>L >RJ>L=/
1904610 MYRTH MYWDH==/
1904613 MYWQJM YWQ[
1973348 JW>MR >MR[
1973351 PWH PH
1973356 >TKMH >T
2056786 XLB LBNWN/
2012717 >DWNJ >DWN/
2012723 KJ> KJ
2012728 T>WMR >MR[
2012729 CPXTKH CPXH/
1934539 >HLBMH >HLJBMH/
1913484 HNH HN
1913487 J<ZWR <ZR[
1913488 LJ> L
1913490 HW>H HW>
1913492 HNH HN
1913498 J>KWLM >KL[
1931892 HJ>H HJ>
1910140 >SWR >SJR=/
1910146 XWCK XCK/
2039763 NW>M N>M/
2044882 M <L
2053494 KJ> KJ
2053498 M>WD M>D/
1973525 KJ> KJ
1973527 >KBDKH KBD[
1973528 MW>DH M>D/
1973532 TW>MR >MR[
1973539 QWBH QBB[
2041330 HJ> HJH[
2087975 >WRKH >WR/
2087977 >MTKH >MT/
2056232 >JNH >JN/
2056704 MT>MWT T>M[
1899630 >WQR JQR[
2059136 > MLK/
2059138 > >LH/
2059139 <LJ <LJ/
2

...

1967932 >CH >LH
2080397 CBR CBWR/
2080401 JLPT JBLT/
2080405 JBLT JLPT/
2040615 JWMR >MR[
1944550 TLXYW LXY[
1912677 QRWBW QRB[
1912682 ZW>T Z>T
1912685 RWC R>C/
1907678 >LWHJKH >LHJM/
1907681 RB RB_CQH/
1907682 CQH RB_CQH/
1907687 >DWNJW >DWN/
1907690 >LWHJM >LHJM/
1907699 >LWHJKH >LHJM/
1907710 H MY>[
1907711 ZW>T ZH
1932336 KWH KH
1932342 >TMH >TM
1932343 R>JTMH R>H[
1932359 XWRBH XRBH=/
2083550 >LJKH >L
1949942 JMNK JMJN/
1915181 LHMH L
1915186 XWMWTJ XWMH/
1915199 LHMH L
1925047 XMTJ XWMH/
1993632 M >MH/
2060821 R>JTJHW R>H[
2060853 JRMWSHW RMS[
1930726 KTBTH KTB[
2057588 XVW> XV>/
2057594 NWD NDH/
2057598 HZJLW ZLL[
2057599 KJ> KJ
2057603 HJ>H HJ>
1911890 BJ> B
1911894 PJ> PH/
1911900 KJ> KJ
1911901 LJ> L
1911904 BJRK BRK/
1946349 JW>MR >MR[
1901405 <W<JJM <W<JM/
2017526 NSK MSK[
1907885 L<JR <JR/
1907887 SPRJJM SPRWJM=/
1907889 N< HN</
1907893 CWMRWN CMRWN/
1921531 L<JR <JR/
2001175 QDMNJJM QDMNJ/
2057123 HW>H HW>
2057131 JT NTN[
2057132 L >L
1899163 JC<C< C<<[
1899166 XWR XR/
1

2085976 LBJ LBB/
2085980 SR<PJ FR<PJM/
2084230 <BDKH <BD/
2084231 >MRTKH >MRH/
2084234 JR>TKH JR>[
2042937 <BWTWT <BT/
2042944 <WL <L/
1916681 THRHR TDHR/
1926023 BR>C BRWC/
1926024 TRHR TDHR/
1979695 FLMTKK FMLH/
2073522 PWRQ PRQ[
2002250 T>P >PH[
2063022 LHMH L
2063024 LKMH L
2063026 >WHLJKMH >HL/
2066698 >HLJLJKM >HL/
2068124 LHMH L
2068126 LKMH L
2068128 >WHLJKMH >HL/
1914144 >LWHJK >LHJM/
1976683 JW>MRW >MR[
1976685 YW>N Y>N/
1976688 MQNJNW MQNH/
1976689 PWH PH
1999270 HQRW>JM QR>[
1999274 CB<JM CLC/
1902590 TLRCJCH TRCJC=/
1971711 MVJ MVH/
2100666 JDKH DKH[
2100672 XLK>JM K>H/
1900482 B>R B>R_>JLJM/
1900483 >JLJM B>R_>JLJM/
1919514 B>R B>R_>JLJM/
1919515 >JLJM B>R_>JLJM/
2061882 > MLKW/
2061888 > MLKW/
2061891 > <LM/
2061895 <LMJ <LM/
2061896 > <LM/
2084589 <DWWTJKH <DWT/
2073479 >MWTJNW >M/
2042147 >LWHJHM >LHJM/
1976833 JW>MRW >MR[
1976839 W R>WBN/
1976845 MWCH MCH=/
1976848 <BDJKH <BD/
1976852 >DWNJ >DWN/
1891874 BCLTH BCL[
1971763 MVJ MVH/
2100572 BYRH YRH/
1900349 LJLH LJL/


1916240 KWLNW KL/
1916243 HGW> HGH[
1909506 <WYMH <YMH/
1918021 HWYJTJ JY>[
1918031 JRCWHJ JRC[
1977966 JW>MRW >MR[
1977968 >DWNJ >DWN/
1977981 BNJ BT/
1994247 MHW MHWMH/
1994248 MH MHWMH/
2006699 GWZZJM GZZ[
2006703 B<L B<L_XYWR/
2006704 XYWR B<L_XYWR/
2006711 L KL/
2054161 TSKH SKK[
1956135 MYRJJM MYRJM/
1956148 MYRJJM MYRJM/
1913959 L LKN
1913960 KN LKN
1913963 ZW>T Z>T
1913965 CKWRT CKR/
2000486 LHM LJLH/
1905408 VMJTM VM>[
1905415 >PWDWT >PDH/
1896068 M<VPWT MVPXT/
1974337 >HRWN >HRN/
1974339 KWHN KHN/
1974348 RWMX RMX/
2051682 JW>MRW >MR[
2051684 GWJJM GWJ/
2083684 GWJJM GWJ/
2032218 HGLWH GLH[
2084840 >MRTKH >MRH/
2084841 MW>DH M>D/
2084843 <BDKH <BD/
2072744 BT BT_CB</
2072745 CB< BT_CB</
2061426 PT PTBG/
2061427 BGW PTBG/
2042404 >ZRW<WTM ZRW</
1909332 JRBQ RQB[
1909338 BCQ BQC[
1909341 HWKJN KWN[
1918211 KJ> KJ
1918213 FJF FWF[
1918215 GJL GJL[
1918221 KJ> KJ
1998252 MHMT MHWMH/
1998264 >LWHJM >LHJM/
2003100 B BJT_LXM/
2003101 BJT BJT_LXM/
2003102 LXM BJT_LXM/
2003112 J>WR >W

1917554 QWDCW QDC/
1911320 KJ> KJ
1911323 JYRTJKH JYR[
1911329 TF>NJ NCH[
2038983 >KLTMH >KL[
2038985 FB<TMH FB<[
2038990 >TKMH >T
2084408 CWGG CGG[
2084411 >MRTKH >MRH/
2053374 HWPKJ HPK[
2058818 > MLK/
2058823 > <BJDH/
2058831 <BD <BD_NGW/
2058832 NGW <BD_NGW/
2058838 > MLK/
1897335 L LKN
1897336 KN LKN
1897339 HWH HW>
1897340 LKMH L
1897352 <MNW <MNW_>L/
1897353 >L <MNW_>L/
2029057 L LKN
2029058 KN LKN
2029074 <MNW <MNW_>L/
2029075 >L <MNW_>L/
2083474 <WMDWT <MD[
1990365 MPT MWPT/
1911453 JTJSD JSD[
2038799 NWGHM NGH/
2084691 >MRTKH >MRH/
2084698 MCBRJ FBR/
2058549 > PRZL/
2058550 KLQBL QBL/
2058553 > PRZL/
2058558 > KL/
2058562 > PRZL/
2058571 >R< >R</
2058572 > MLK/
1999752 JBZWHW BZH[
1999790 >JC XRC[
1901009 YL YLYL/
1901010 YL YLYL/
2047746 <LJKH <L
2047754 <WZJ GZH[
1928290 ZRW<KH ZRW</
1898712 XWYB XYB[
1898719 MNJPJW NWP[
2080592 TM QRB[
1996902 H HJH[
1996904 W <WD/
2008087 JCM<>LJ JFR>LJ/
2084637 TWRTKH TWRH/
2098204 HTQCCW QCC[
2098206 QCW QCC[
2058411 > PRZL/
2058413 > X

1910518 TXTJKH TXT/
1977208 MQHLWT MQHLT/
1961093 BWQR BQR=/
1900045 BWMTJ BMH/
2060065 GBRJ GBR/
2060066 > GBR/
2045928 >NWKJ >NKJ
2009541 JCBJ JCBJ=/
2009542 BNB NB/
2009550 QNW QJN/
2009559 XWRH XGWRH/
1972007 >LWHJKMH >LHJM/
1953383 MYRJJM MYRJ/
2055824 KLWTJH KLH/
1910839 QNJTH QNH[
1910840 LJ> L
1910846 ZBXJKH ZBX/
1910852 XV>WTJKH XV>T/
1910855 <WNKH <WN/
1977106 YB>WTM YB>/
1977109 MWCH MCH=/
1977111 >HRWN >HRN/
2088347 >WDKH JDH[
2007074 <MJXWD <MJHWD/
1900218 <LJKMH <L
1900224 CKMKH CKM/
1974443 RW>C R>C/
2037273 NJNW> NJNWH/
2067480 MYWKH YWH[
2067482 JW JWM/
2067483 M JWM/
2084964 >NWKJ >NKJ
2084966 >MRTKH >MRH/
1910740 <WZWZ <ZWZ=/
1910742 JCKWBW CKB[
1966215 H HXJRWT/
1966216 XJRT HXJRWT/
1983468 MMLKTW MMLKH/
2033165 W R<=/
1903227 XWRB XRB=/
1900059 RW>JK R>H[
1900062 >LJKH >L
1974856 ZBWLWN ZBWLNJ/
2057285 >WZN >ZN/
2040815 RW>CW R>C/
2036409 DMWTM DMWT/
1931316 MPRJST PRS[
1931319 CS<T CS</
1917342 LHMH L
2043447 >SWPW >SP[
1974701 <DJ <RJ=/
1974704 <DJ <RJ/
1960943 J

In [ ]:
# check 2060601 >
# in the dss package > is a distinct word (lex '@>'), in contrast to the BHSA

# 2060598 H MLKW/ is a similar case

In [ ]:
# check 2070064	4Q142	Deuteronomy	6	7	KTKH	HLk	HLK[	suff	verb

In [ ]:
# check een of twee woorden? 20316441	4Q74	Ezekiel	1	23	LHNH	L:	HNH=	suff	prps


Collect the data in a dataframe.

In [79]:
df = pd.DataFrame(list(zip(tf_word_id, scrolls, books, chapters, verses, words_dss, lexs_dss, lexs_etcbc, poss_dss, poss_etcbc, second)), 
               columns =['tf_word_id', 'scroll','book','chapter', 'verse', 'g_cons', 'lex_dss', 'lex_etcbc', 'pos_dss', 'pos_etcbc', 'second_assignment']) 

df_new = df.sort_values(['book', 'scroll', 'chapter', 'verse'], ascending=[True, True, True, True])
df_new

tf_word_id scroll       book  chapter  verse   g_cons    lex_dss  \
106925     2013632   4Q54    1_Kings        7     20        W         W:   
106926     2013633   4Q54    1_Kings        7     20     KTRT   K.OTERET   
106927     2013634   4Q54    1_Kings        7     20       <L        <AL   
106928     2013635   4Q54    1_Kings        7     20      CNJ    C:NAJIm   
106929     2013636   4Q54    1_Kings        7     20        H         HA   
106930     2013637   4Q54    1_Kings        7     20   <MWDJM    <AM.W.D   
106931     2013638   4Q54    1_Kings        7     20       GM       G.Am   
106932     2013639   4Q54    1_Kings        7     20        M        MIn   
106933     2013640   4Q54    1_Kings        7     20      M<L      MA<AL   
106934     2013641   4Q54    1_Kings        7     20        M        MIn   
106935     2013642   4Q54    1_Kings        7     20        L         L:   
106936     2013643   4Q54    1_Kings        7     20      <MT     <UM.@H   
106937     2013644   4Q54    1_Kings        7     20        H         HA   
106938     2013645   4Q54    1_Kings        7     20      BVN     B.EVEn   
106939     2013646   4Q54    1_Kings        7     20      >CR     >:ACER   
106940     2013647   4Q54    1_Kings        7     20        L         L:   
106941     2013648   4Q54    1_Kings        7     20      <BR      <;BER   
106942     2013649   4Q54    1_Kings        7     20     FBKH    F:B@K@H   
106943     2013650   4Q54    1_Kings        7     20        W         W:   
106944     2013651   4Q54    1_Kings        7     20        H         HA   
106945     2013652   4Q54    1_Kings        7     20   RMWNJM    RIM.OWn   
106946     2013653   4Q54    1_Kings        7     20    M>TJM      M;>@H   
106947     2013654   4Q54    1_Kings        7     20     VRJM       VW.R   
106948     2013655   4Q54    1_Kings        7     20     SBJB     S@BIJB   
106949     2013656   4Q54    1_Kings        7     20       <L        <AL   
106950     2013657   4Q54    1_Kings        7     20        H         HA   
106951     2013658   4Q54    1_Kings        7     20     KTRT   K.OTERET   
106952     2013659   4Q54    1_Kings        7     20        H         HA   
106953     2013660   4Q54    1_Kings        7     20     CNJT      C;NIJ   
130275     2013662   4Q54    1_Kings        7     21        W         W:   
...            ...    ...        ...      ...    ...      ...        ...   
194287     2098822  Mur88  Zephaniah        3     20        H         HA   
194288     2098823  Mur88  Zephaniah        3     20      HJ>       HIJ>   
194289     2098824  Mur88  Zephaniah        3     20     >BJ>        BW>   
194290     2098825  Mur88  Zephaniah        3     20     >TKM        >;T   
194291     2098826  Mur88  Zephaniah        3     20        W         W:   
194292     2098827  Mur88  Zephaniah        3     20        B        B.:   
194293     2098828  Mur88  Zephaniah        3     20       <T        <;T   
194294     2098829  Mur88  Zephaniah        3     20     QBYJ        QBy   
194295     2098830  Mur88  Zephaniah        3     20     >TKM        >;T   
194296     2098831  Mur88  Zephaniah        3     20       KJ       K.IJ   
194297     2098832  Mur88  Zephaniah        3     20      >TN        NTn   
194298     2098833  Mur88  Zephaniah        3     20     >TKM        >;T   
194299     2098834  Mur88  Zephaniah        3     20        L         L:   
194300     2098835  Mur88  Zephaniah        3     20       CM        C;m   
194301     2098836  Mur88  Zephaniah        3     20        W         W:   
194302     2098837  Mur88  Zephaniah        3     20        L         L:   
194303     2098838  Mur88  Zephaniah        3     20     THLH  T.:HIL.@H   
194304     2098839  Mur88  Zephaniah        3     20        B        B.:   
194305     2098840  Mur88  Zephaniah        3     20       KL       K.OL   
194306     2098841  Mur88  Zephaniah        3     20      <MJ        <Am   
194307     2098842  Mur88  Zephaniah        3     20    

Save the data in a csv file and print the mapping_dict. 

In [80]:
df_new.to_csv("lexemes_pos_all_bib_books.csv", index=False)

In [29]:
with open("mapping_dict.pkl", "wb") as dill_file:
    dill.dump(mapping_dict, dill_file)

pprint(mapping_dict)